In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
import sys
import os
import time
import numpy as np
from functools import partial
import itertools


In [3]:
import pydrake
import meshcat

from pydrake.all import BsplineTrajectoryThroughUnionOfHPolyhedra, IrisInConfigurationSpace, IrisOptions
from pydrake.common import FindResourceOrThrow
from pydrake.geometry import SceneGraph
from pydrake.math import RigidTransform, RollPitchYaw
from pydrake.multibody.optimization import CalcGridPointsOptions, Toppra
from pydrake.multibody.parsing import LoadModelDirectives, Parser, ProcessModelDirectives
from pydrake.multibody.plant import MultibodyPlant, AddMultibodyPlantSceneGraph
from pydrake.multibody.tree import RevoluteJoint
from pydrake.solvers.mathematicalprogram import MathematicalProgram, Solve
from pydrake.solvers.mosek import MosekSolver
from pydrake.systems.analysis import Simulator
from pydrake.systems.framework import DiagramBuilder
from pydrake.systems.primitives import TrajectorySource
from pydrake.trajectories import PiecewisePolynomial
from pydrake.all import Variable, Expression, RotationMatrix
from pydrake.all import MultibodyPositionToGeometryPose, ConnectMeshcatVisualizer, Role, Sphere
from pydrake.all import (
    ConvexSet, HPolyhedron, Hyperellipsoid,
    MathematicalProgram, Solve, le, IpoptSolver,
    Role, Sphere, VPolytope,
    Iris, IrisOptions, MakeIrisObstacles, Variable
)
from pydrake.all import (
    eq, SnoptSolver,
    Sphere, Ellipsoid, GeometrySet,
    RigidBody_, AutoDiffXd, initializeAutoDiff, InverseKinematics
)

import pydrake.symbolic as sym
import symbolic_parsing_helpers as symHelpers

from meshcat import Visualizer

import mcubes

import ipywidgets as widgets
from IPython.display import display 

# Setup meshcat
from meshcat.servers.zmqserver import start_zmq_server_as_subprocess
proc, zmq_url, web_url = start_zmq_server_as_subprocess(server_args=[])
proc2, zmq_url2, web_url2 = start_zmq_server_as_subprocess(server_args=[])

# Sporadically need to run `pkill -f meshcat`

from symbolic_parsing_helpers import generate_rationalize_trig_expr_rules
from symbolic_parsing_helpers import xreplace
from symbolic_parsing_helpers import NotRationalFunctionException
# from symbolic_parsing_helpers import rationalize_trig_expr
from pydrake.all import RationalFunction
snopt = SnoptSolver()
def xreplace(expr, rules):
        if isinstance(expr, float) or isinstance(expr, sym.Variable):
            return expr
        assert isinstance(expr, sym.Expression), expr
        for old, new in rules:
            if expr.EqualTo(old):
                return new
        ctor, old_args = expr.Deconstruct()
        new_args = [xreplace(e, rules) for e in old_args]
        return ctor(*new_args)

def MakeFromHPolyhedronOrEllipseSceneGraph(query, geom, expressed_in=None):
    shape = query.inspector().GetShape(geom)
    if isinstance(shape, (Sphere, Ellipsoid)):
        return Hyperellipsoid(query, geom, expressed_in)
    return HPolyhedron(query, geom, expressed_in)
def MakeFromVPolytopeOrEllipseSceneGraph(query, geom, expressed_in=None):
    shape = query.inspector().GetShape(geom)
    print(geom)
    if isinstance(shape, (Sphere, Ellipsoid)):
        return Hyperellipsoid(query, geom, expressed_in)
    return VPolytope(query, geom, expressed_in)


from pydrake.all import RationalForwardKinematics, FindBodyInTheMiddleOfChain

In [4]:
# prog = MathematicalProgram()

# x = [sym.Variable("x{}".format(i)) for i in range(3)]
# prog.AddIndeterminates(x)
# poly, Q = prog.NewSosPolynomial(sym.Variables(x),2)
# poly.SetIndeterminates(sym.Variables(x))
# print(prog)
# prog.AddSosConstraint(poly)
# print(prog)

In [5]:
x = sym.Variable('x')
r1 = RationalFunction(sym.Polynomial(2*x+1), sym.Polynomial(x**2-1))
r2 = RationalFunction(sym.Polynomial(2*x+1), sym.Polynomial(x**2-1))
r3 = RationalFunction(sym.Polynomial(2*x+1), sym.Polynomial(x+1)*sym.Polynomial(x-1))
r4 = RationalFunction(sym.Polynomial(2*x+1), sym.Polynomial(x+1))

print(r1+r2)
print(r1+r3)
print(r1+r4)

(2*1 + 4*x) / (-1*1 + 1*x^2)
(2*1 + 4*x) / (-1*1 + 1*x^2)
(1*x + 3*x^2 + 2*x^3) / (-1*1 + -1*x + 1*x^2 + 1*x^3)


# Build simulation Environment

In [6]:
simple_collision = True
# gripper_welded = True

vis = Visualizer(zmq_url=zmq_url)
vis.delete()
vis2 = Visualizer(zmq_url=zmq_url2)
vis2.delete()

display(vis.jupyter_cell())

builder = DiagramBuilder()
plant, scene_graph = AddMultibodyPlantSceneGraph(builder, time_step=0.001)
parser = Parser(plant)
parser.package_map().Add( "wsg_50_description", os.path.dirname(FindResourceOrThrow(
            "drake/manipulation/models/wsg_50_description/package.xml")))

directives_file = FindResourceOrThrow("drake/sandbox/planar_iiwa_simple_collision_welded_gripper.yaml") \
    if simple_collision else FindResourceOrThrow("drake/sandbox/planar_iiwa_dense_collision_welded_gripper.yaml")
directives = LoadModelDirectives(directives_file)
models = ProcessModelDirectives(directives, plant, parser)


q0 = [-0.2, -1.2, 1.6]
index = 0
for joint_index in plant.GetJointIndices(models[0].model_instance):
    joint = plant.get_mutable_joint(joint_index)
    if isinstance(joint, RevoluteJoint):
        joint.set_default_angle(q0[index])
        index += 1

plant.Finalize()

visualizer = ConnectMeshcatVisualizer(builder, scene_graph, zmq_url=zmq_url, delete_prefix_on_load=False)

diagram = builder.Build()
visualizer.load()
context = diagram.CreateDefaultContext()
plant_context = plant.GetMyContextFromRoot(context)
slider_context = plant.CreateDefaultContext()
diagram.Publish(context)
query = scene_graph.get_query_output_port().Eval(scene_graph.GetMyContextFromRoot(context))


    
ik = InverseKinematics(plant, plant_context)
collision_constraint = ik.AddMinimumDistanceConstraint(0.001, 0.01)


inspector = query.inspector()
pairs = inspector.GetCollisionCandidates()


geom_ids = inspector.GetGeometryIds(GeometrySet(inspector.GetAllGeometryIds()), Role.kProximity)
HPolyhedronSets = {geom:MakeFromHPolyhedronOrEllipseSceneGraph(query, geom, inspector.GetFrameId(geom)) for geom in geom_ids}
VPolyhedronSets = {geom:MakeFromVPolytopeOrEllipseSceneGraph(query, geom, inspector.GetFrameId(geom)) for geom in geom_ids}



body_indexes_by_geom_id = {geom:
                           plant.GetBodyFromFrameId(inspector.GetFrameId(geom)).index() for geom in geom_ids} 

You can open the visualizer by visiting the following URL:
http://127.0.0.1:7000/static/
You can open the visualizer by visiting the following URL:
http://127.0.0.1:7001/static/


Connecting to meshcat-server at zmq_url=tcp://127.0.0.1:6000...
You can open the visualizer by visiting the following URL:
http://127.0.0.1:7000/static/
Connected to meshcat-server.
<GeometryId value=71>
<GeometryId value=79>
<GeometryId value=113>
<GeometryId value=115>
<GeometryId value=117>
<GeometryId value=85>
<GeometryId value=91>


# Sliders

In [53]:
forward_kin = RationalForwardKinematics(plant)
q_star = np.zeros(forward_kin.t().shape[0])
t_kin = forward_kin.t()
def convert_RationalForwardPoseList_to_TransformExpressionList(pose_list):
    ret = []
    for p in pose_list:
        ret.append(p.asRigidTransformExpr())
    return ret

def convert_t_to_q(t):
    q =np.arctan2(2*t/(1+t**2), (1-t**2)/(1+t**2))
    return q

def convert_q_to_t(t):
    q =np.tan(t/2)
    return q

def eval_cons(q0, q1, q2, c, tol):
        return 1-1*float(c.evaluator().CheckSatisfied([q0, q1, q2], tol))
    
col_func_handle = partial(eval_cons, c=collision_constraint, tol=0.01)


def eval_cons_rational(t0, t1, t2, c, tol):
        q = convert_t_to_q(np.array([t0, t1, t2])) 
        return 1-1*float(c.evaluator().CheckSatisfied(q, tol))

col_func_handle_rational = partial(eval_cons_rational, c=collision_constraint, tol=0.01)
link_poses_by_body_index_rat_pose = forward_kin.CalcLinkPoses(q_star, 
                                                         plant.world_body().index())
link_poses_by_body_index_multilinear_pose = forward_kin.CalcLinkPosesAsMultilinearPolynomials(q_star, 
                                                         plant.world_body().index())

X_WA_list = convert_RationalForwardPoseList_to_TransformExpressionList(link_poses_by_body_index_rat_pose)
X_WA_multilinear_list = [(r.rotation().copy(), r.translation().copy()) for r in link_poses_by_body_index_multilinear_pose]
geomA, geomB = next(iter(pairs))
index = FindBodyInTheMiddleOfChain(plant, body_indexes_by_geom_id[geomA], body_indexes_by_geom_id[geomB])
print(index)

t_space_vertex_position_by_geom_id ={}
for geom in geom_ids:
    VPoly = VPolyhedronSets[geom]
    num_verts = VPoly.vertices().shape[1]
    X_WA = X_WA_list[int(body_indexes_by_geom_id[geom])]
    R_WA = X_WA.rotation().matrix()
    p_WA = X_WA.translation()
    vert_pos = R_WA@(VPoly.vertices())+ np.repeat(p_WA[:, np.newaxis],num_verts,1)
    t_space_vertex_position_by_geom_id[geom] = vert_pos


BodyIndex(4)


In [8]:
q_low = plant.GetPositionLowerLimits()
q_high = plant.GetPositionUpperLimits()
t_low = forward_kin.ComputeTValue(q_low,q_star)
t_high = forward_kin.ComputeTValue(q_high,q_star)
print(t_low)
print(t_high)


[-1.73205081 -1.73205081 -1.73205081]
[1.73205081 1.73205081 1.73205081]


In [76]:




def eval_cons(q0, q1, q2, c, tol):
        return 1-1*float(c.evaluator().CheckSatisfied([q0, q1, q2], tol))

col_func_handle = partial(eval_cons, c=collision_constraint, tol=0.01)

def eval_cons_rational(t0, t1, t2, c, tol):
    q = convert_t_to_q(np.array([t0, t1, t2]).reshape(1,-1)).squeeze() 
    return col_func_handle(*q)
   
col_func_handle_rational = partial(eval_cons_rational, c=collision_constraint, tol=0.01)

def showres(q):
#     set_joint_ang(q[0],0)
#     set_joint_ang(q[1],1)
#     set_joint_ang(q[2],2)
    plant.SetPositions(slider_context, q)
    col = col_func_handle(*q)
    t = convert_q_to_t(np.array(q).reshape(1,-1)).squeeze()
    if col:
        vis2["t"].set_object(
                meshcat.geometry.Sphere(0.1), meshcat.geometry.MeshLambertMaterial(color=0xFFB900))
        vis2["t"].set_transform(
                meshcat.transformations.translation_matrix(t))
    else:
        vis2["t"].set_object(
                meshcat.geometry.Sphere(0.1), meshcat.geometry.MeshLambertMaterial(color=0x3EFF00))
        vis2["t"].set_transform(
                meshcat.transformations.translation_matrix(t))
    diagram.Publish(context)
    print("              ", end = "\r")
    print(col , end = "\r")
    
def showres_t(t):
    q = convert_t_to_q(t)
    showres(q)

sliders = []
sliders.append(widgets.FloatSlider(min=t_low[0], max=t_high[0], value=0, description='t0'))
sliders.append(widgets.FloatSlider(min=t_low[1], max=t_high[1], value=0, description='t1'))
sliders.append(widgets.FloatSlider(min=t_low[2], max=t_high[2], value=0, description='t2'))

q = q0.copy()
t = convert_q_to_t(np.array(q))
def handle_slider_change(change, idx):
    t[idx] = change['new']
    print(q, end="\r")
    showres_t(t)
    plane_callback(t)
    
idx = 0
for slider in sliders:
    slider.observe(partial(handle_slider_change, idx = idx), names='value')
    idx+=1

In [77]:
for slider in sliders:
    display(slider)

display(vis.jupyter_cell())
display(vis2.jupyter_cell())


FloatSlider(value=0.0, description='t0', max=1.7320508075624863, min=-1.7320508075624863)

FloatSlider(value=0.0, description='t1', max=1.7320508075624863, min=-1.7320508075624863)

FloatSlider(value=0.0, description='t2', max=1.7320508075624863, min=-1.7320508075624863)

{Variable('t[0]', Continuous): -0.10033467208545055, Variable('t[1]', Continuous): 0.06795, Variable('t[2]', Continuous): 1.0296385570503641}
6733.0564152142688*1 + 106.31626291713681*t[2] + 1340.8130199441764*t[2]^2 + 696.10257861675768*t[1] + 1143.7034623504385*t[1] * t[2] + 3166.5489423408299*t[1]^2 + -3057.7618107826529*t[0] + -364.03217886027574*t[0] * t[2] + 4883.3573380367216*t[0] * t[1] + 2536.2717823042726*t[0]^2
{Variable('t[0]', Continuous): -0.10033467208545055, Variable('t[1]', Continuous): 0.06795, Variable('t[2]', Continuous): 1.0296385570503641}
4.0384806288745958e-10*1 + 2.2154528311439724e-10*t[2] + -1.4539120484322882e-10*t[2]^2 + -3.667451065952887e-10*t[1] + -4.1478322873260979e-11*t[1] * t[2] + -3.1589551452313479e-12*t[1]^2 + -5.0526771122507908e-10*t[0] + -6.9120821540193858e-11*t[0] * t[2] + 3.0501550987813448e-10*t[0] * t[1] + -1.9441123077021044e-10*t[0]^2
{Variable('t[0]', Continuous): -0.10033467208545055, Variable('t[1]', Continuous): 0.06795, Variable('t[

{Variable('t[0]', Continuous): -0.10033467208545055, Variable('t[1]', Continuous): -0.03205, Variable('t[2]', Continuous): 1.0296385570503641}
6733.0564152142688*1 + 106.31626291713681*t[2] + 1340.8130199441764*t[2]^2 + 696.10257861675768*t[1] + 1143.7034623504385*t[1] * t[2] + 3166.5489423408299*t[1]^2 + -3057.7618107826529*t[0] + -364.03217886027574*t[0] * t[2] + 4883.3573380367216*t[0] * t[1] + 2536.2717823042726*t[0]^2
{Variable('t[0]', Continuous): -0.10033467208545055, Variable('t[1]', Continuous): -0.03205, Variable('t[2]', Continuous): 1.0296385570503641}
4.0384806288745958e-10*1 + 2.2154528311439724e-10*t[2] + -1.4539120484322882e-10*t[2]^2 + -3.667451065952887e-10*t[1] + -4.1478322873260979e-11*t[1] * t[2] + -3.1589551452313479e-12*t[1]^2 + -5.0526771122507908e-10*t[0] + -6.9120821540193858e-11*t[0] * t[2] + 3.0501550987813448e-10*t[0] * t[1] + -1.9441123077021044e-10*t[0]^2
{Variable('t[0]', Continuous): -0.10033467208545055, Variable('t[1]', Continuous): -0.03205, Variable(

...

1.50686127694037
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.23205}
1838.0133663624865*1 + -1721.7732551091979*t[2] + 634.19648307450836*t[2]^2 + 3777.0788465469495*t[1] + 855.89522654564598*t[1] * t[2] + 941.93914789984615*t[1]^2 + -5740.8305828853363*t[0] + -761.37913704693437*t[0] * t[2] + 1953.9188827305454*t[0] * t[1] + 1200.6384532483567*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.23205}
-4279.6432844098244*1 + 732.92055541681918*t[2] + 3475.6741378880483*t[2]^2 + -3140.8583547393923*t[1] + -1565.1962678854782*t[1] * t[2] + 3671.2260991434655*t[1]^2 + 5855.8571764706139*t[0] + 1211.5359462457698*t[0] * t[2] + -3029.0975632978088*t[0] * t[1] + 4013.6002054641276*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.23205}
-5068.8836585296858*1 + -1207.5361733665695*t[2] 

[ 1178.4736127  -6193.11316155 -7559.61318293], 1346.352905505471
7.679478594798696
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.13205}
3540.1870346042556*1 + -427.37863391722072*t[2] + 878.98187315449832*t[2]^2 + 1582.8531253059475*t[1] + 785.12191030380734*t[1] * t[2] + 1347.2411812062815*t[1]^2 + -3530.2080223503845*t[0] + -696.45050852936572*t[0] * t[2] + 3349.845584717953*t[0] * t[1] + 1147.6736726334129*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.13205}
2.477847901301729e-09*1 + 1.452333346087466e-09*t[2] + -1.7182115848265821e-09*t[2]^2 + -1.7026272021951528e-09*t[1] + 3.1925814578266715e-09*t[1] * t[2] + -2.188912678479881e-10*t[1]^2 + 6.5871577198991102e-10*t[0] + -5.3224246606471125e-09*t[0] * t[2] + 2.8585116053371165e-09*t[0] * t[1] + -2.1368517040628897e-10*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuo

{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.13205}
1838.0133679315695*1 + -1721.7732542104193*t[2] + 634.19648308890021*t[2]^2 + 3777.0788454121275*t[1] + 855.89522671959753*t[1] * t[2] + 941.93914793526892*t[1]^2 + -5740.8305815397543*t[0] + -761.37913766503198*t[0] * t[2] + 1953.9188834925965*t[0] * t[1] + 1200.6384532346624*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.13205}
4279.6432848865998*1 + -732.92054269199662*t[2] + -3475.6741376426094*t[2]^2 + 3140.8583465067818*t[1] + 1565.1962724494185*t[1] * t[2] + -3671.2260963015174*t[1]^2 + -5855.8571701835199*t[0] + -1211.5359566597469*t[0] * t[2] + 3029.0975685138201*t[0] * t[1] + -4013.6002045869873*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.13205}
-5068.8836568338074*1 + -1207.5361740420676*t[2] + -375.82721022

{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.03205}
3033.1245434455464*1 + -975.59431674396058*t[2] + 722.39829554463222*t[2]^2 + 2195.1729773943757*t[1] + 882.00590433528191*t[1] * t[2] + 997.39540740794985*t[1]^2 + -4342.0845889660504*t[0] + -937.57772514711928*t[0] * t[2] + 3116.7209611706085*t[0] * t[1] + 895.92143333379659*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.03205}
1921.3410435822011*1 + -860.99074350773583*t[2] + -3036.5052120221867*t[2]^2 + 4144.7259648039253*t[1] + 2225.9559226330989*t[1] * t[2] + -3563.8886245388999*t[1]^2 + -7826.2834794252685*t[0] + -1488.7899744202207*t[0] * t[2] + 4570.6743770965395*t[0] * t[1] + -4158.386894313503*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.03205}
-3334.5969518327465*1 + -1395.9759112792983*t[2] + 46.03361769256

{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.03205}
2386.7584507796282*1 + -1549.6751562171098*t[2] + 665.14424443507346*t[2]^2 + 3332.7804403849968*t[1] + 862.16208838524676*t[1] * t[2] + 941.90209425113153*t[1]^2 + -5543.1262825292097*t[0] + -846.44356549942881*t[0] * t[2] + 2598.0202995787995*t[0] * t[1] + 1020.5249709147668*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.03205}
-3107.679135882277*1 + 917.8263228720582*t[2] + 3346.3421119026598*t[2]^2 + -3504.9080586195264*t[1] + -1794.085647054357*t[1] * t[2] + 3619.8743080201843*t[1]^2 + 6637.7979569410809*t[0] + 1152.5096856728469*t[0] * t[2] + -3558.2338669028031*t[0] * t[1] + 4006.3942617893836*t[0]^2
{Variable('t[0]', Continuous): -0.13205, Variable('t[1]', Continuous): -1.33205, Variable('t[2]', Continuous): -0.03205}
-4660.6290691280201*1 + -1285.5750411736424*t[2] + -184.2329041916243

In [10]:
def visualize_trajectory(traj):
    builder = DiagramBuilder()

    scene_graph = builder.AddSystem(SceneGraph())
    plant = MultibodyPlant(time_step=0.0)
    plant.RegisterAsSourceForSceneGraph(scene_graph)
    parser = Parser(plant)
    parser.package_map().Add( "wsg_50_description", os.path.dirname(FindResourceOrThrow(
                "drake/manipulation/models/wsg_50_description/package.xml")))

    directives_file = FindResourceOrThrow("drake/sandbox/planar_iiwa_simple_collision_welded_gripper.yaml") \
        if simple_collision else FindResourceOrThrow("drake/sandbox/planar_iiwa_dense_collision_welded_gripper.yaml")
    directives = LoadModelDirectives(directives_file)
    models = ProcessModelDirectives(directives, plant, parser)

    q0 = [-0.2, -1.2, 1.6]
    index = 0
    for joint_index in plant.GetJointIndices(models[0].model_instance):
        joint = plant.get_mutable_joint(joint_index)
        if isinstance(joint, RevoluteJoint):
            joint.set_default_angle(q0[index])
            index += 1

    plant.Finalize()

    to_pose = builder.AddSystem(MultibodyPositionToGeometryPose(plant))
    builder.Connect(to_pose.get_output_port(), scene_graph.get_source_pose_port(plant.get_source_id()))

    traj_system = builder.AddSystem(TrajectorySource(traj))
    builder.Connect(traj_system.get_output_port(), to_pose.get_input_port())

    meshcat = ConnectMeshcatVisualizer(builder, scene_graph, zmq_url=zmq_url)

    vis_diagram = builder.Build()

    simulator = Simulator(vis_diagram)
    meshcat.start_recording()
    simulator.AdvanceTo(traj.end_time())
    meshcat.publish_recording()
    with open("/tmp/spp_shelves.html", "w") as f:
        f.write(meshcat.vis.static_html())


# Construct Rational Kinematics

## Marching Cubes Obstacles

In [11]:
N = 50
vertices, triangles = mcubes.marching_cubes_func(tuple(t_low), tuple(t_high), N, N, N, col_func_handle_rational, 0.5)
vis2["collision_constraint"].set_object(
            meshcat.geometry.TriangularMeshGeometry(vertices, triangles),
            meshcat.geometry.MeshLambertMaterial(color=0xff0000, wireframe=True))
# q = q0.copy()
# showres(q)

# Define Iris In T-Space

In [12]:
#  Now IRIS in configuration space, using dReal to solve for the growth volume
# through the nonconvex kinematics.

from pydrake.all import (
    eq, SnoptSolver,
    Sphere, Ellipsoid, GeometrySet,
    RigidBody_, AutoDiffXd, initializeAutoDiff,
)


def TangentPlane(self, point):
    a = 2 * self.A().T @ self.A() @ (point - self.center())
    a = a / np.linalg.norm(a)
    b = a.dot(point)
    return a, b

Hyperellipsoid.TangentPlane = TangentPlane


query = scene_graph.get_query_output_port().Eval(scene_graph.GetMyContextFromRoot(context))

sym_plant = plant.ToSymbolic()
sym_context = sym_plant.CreateDefaultContext()

# For SNOPT test.
snopt = SnoptSolver()



In [13]:
def GrowthVolumeRational(E, X_WA, X_WB, setA, setB, A, b, guess=None):
    snopt = SnoptSolver()
    prog = MathematicalProgram()
    t_kin = forward_kin.t()
    prog.AddDecisionVariables(t_kin)
    
    if guess is not None:
        prog.SetInitialGuess(t_kin, guess)

    prog.AddLinearConstraint(A, b-np.inf, b, t_kin)
    p_AA = prog.NewContinuousVariables(3, "p_AA")
    p_BB = prog.NewContinuousVariables(3, "p_BB")
    setA.AddPointInSetConstraints(prog, p_AA)
    setB.AddPointInSetConstraints(prog, p_BB)
    prog.AddQuadraticErrorCost(E.A().T @ E.A(), E.center(), t_kin)

    p_WA = X_WA.multiply(p_AA+0)
    p_WB = X_WB.multiply(p_BB+0)

    prog.AddConstraint(eq(p_WA, p_WB))
    result = snopt.Solve(prog)
    return result.is_success(), result.get_optimal_cost(), result.GetSolution(t_kin)


In [14]:

def iris_rational_space(query, point, require_containment_points=[], 
                        termination_threshold=2e-2, iteration_limit=100):
    dReal_polytope_tol = 1e-2
    ellipsoid_epsilon = 1e-1
    dim = plant.num_positions()
    lb = plant.GetPositionLowerLimits()
    rational_lb = forward_kin.ComputeTValue(lb, q_star)
    ub = plant.GetPositionUpperLimits()
    rational_ub = forward_kin.ComputeTValue(ub, q_star)
    volume_of_unit_sphere = 4.0*np.pi/3.0
    E = Hyperellipsoid(np.eye(3)/ellipsoid_epsilon, point)
    best_volume = ellipsoid_epsilon**dim * volume_of_unit_sphere
    
    link_poses_by_body_index_rat_pose = forward_kin.CalcLinkPoses(q_star, 
                                                         plant.world_body().index())
    X_WA_list = convert_RationalForwardPoseList_to_TransformExpressionList(link_poses_by_body_index_rat_pose)

    inspector = query.inspector()
    pairs = inspector.GetCollisionCandidates()

    P = HPolyhedron.MakeBox(rational_lb, rational_ub)
    A = np.vstack((P.A(), np.zeros((10*len(pairs),3))))  # allow up to 10 faces per pair.
    b = np.concatenate((P.b(), np.zeros(10*len(pairs))))

    geom_ids = inspector.GetGeometryIds(GeometrySet(inspector.GetAllGeometryIds()), Role.kProximity)
    sets = {geom:MakeFromHPolyhedronOrEllipseSceneGraph(query, geom, inspector.GetFrameId(geom)) for geom in geom_ids}
    body_indexes_by_geom_id = {geom:
                               plant.GetBodyFromFrameId(inspector.GetFrameId(geom)).index() for geom in geom_ids} 
    
    #Turn onto true to certify regions using SOS at each iteration.
    certify = False
    # refine polytopes if not certified collision free
    refine = False and certify
        
    iteration = 0
    num_faces = 2*len(lb)
    while True:
        ## Find separating hyperplanes

        for geomA, geomB in pairs:
            print(f"geomA={inspector.GetName(geomA)}, geomB={inspector.GetName(geomB)}")
            # Run snopt at the beginning
            while True:
                X_WA = X_WA_list[int(body_indexes_by_geom_id[geomA])]
                X_WB = X_WA_list[int(body_indexes_by_geom_id[geomB])]
                success, growth, qstar = GrowthVolumeRational(E,
                    X_WA, X_WB,
                    sets[geomA], sets[geomB], 
                    A[:num_faces,:], b[:num_faces] - dReal_polytope_tol, 
                    point)
                qstar = qstar.squeeze()
                if success:
                    print(f"snopt_example={qstar}, growth = {growth}")
                    # Add a face to the polytope
                    A[num_faces,:], b[num_faces] = E.TangentPlane(qstar)
                    num_faces += 1
                else:
                    break

            if certify:
                pass
            

        if any([np.any(A[:num_faces,:] @ t > b[:num_faces]) for t in require_containment_points]):
            print("terminating because a required containment point would have not been contained")
            break

        P = HPolyhedron(A[:num_faces,:],b[:num_faces])

        E = P.MaximumVolumeInscribedEllipsoid()
        print(iteration)

        iteration += 1
        if iteration >= iteration_limit:
            break

        volume = volume_of_unit_sphere / np.linalg.det(E.A())
        if volume - best_volume <= termination_threshold:
            break
        best_volume = volume

    return P

In [15]:
seed_points = np.tan(np.array([[0.0, -2.016, 1.975], # in tight
                        [-1, -2, 0.5],        # neutral pose
                        [0.3, -0.8, 0.5],     # above shelf
                        [0.25, -1.6, -0.25],  # in shelf 1
                        [0.07, -1.8, -0.2],   # leaving shelf 1
                        [-0.1, -2, -0.3]])    # out of shelf 1
                        /2)
for i in range(seed_points.shape[0]):
    vis2['seedpoints']["seedpoint"+str(i)].set_object(
                meshcat.geometry.Sphere(0.1), meshcat.geometry.MeshLambertMaterial(color=0xFFB900))
    vis2['seedpoints']["seedpoint"+str(i)].set_transform(
                meshcat.transformations.translation_matrix(seed_points[i,:]))

# traj = PiecewisePolynomial.FirstOrderHold(np.array([0, 1]), np.array([seed_points[4], seed_points[1]]).T)
# visualize_trajectory(traj)

In [16]:

regions = []
ellipses = []
for i in range(seed_points.shape[0]):
    
    start_time = time.time()
    hpoly = iris_rational_space(query, seed_points[i,:], require_containment_points=[seed_points[i,:]], iteration_limit=100)
    ellipse = hpoly.MaximumVolumeInscribedEllipsoid()
    print("Time: %6.2f \tVolume: %6.2f \tCenter:" % (time.time() - start_time, ellipse.Volume()),
          ellipse.center(), flush=True)
    regions.append(hpoly)
    ellipses.append(ellipse)

print("SUCCESS")

geomA=iiwa::link7, geomB=shelves::top
snopt_example=[ 0.25686152 -0.44650254  1.37305101], growth = 138.27790339845825
geomA=iiwa::link7, geomB=wsg::right_collision
geomA=wsg::left_collision, geomB=wsg::right_collision
geomA=wsg::right_collision, geomB=shelves::shelf_upper
snopt_example=[ 0.14471298 -0.66482365  0.73909564], growth = 147.06126401711242
snopt_example=[ 0.26684134 -0.53520202  0.93115289], growth = 151.49619658550938
geomA=wsg::body_collision, geomB=shelves::top
geomA=wsg::body_collision, geomB=shelves::shelf_upper
snopt_example=[ 0.32551918 -0.53379534  1.10297422], growth = 138.142516784699
geomA=wsg::left_collision, geomB=shelves::top
geomA=wsg::right_collision, geomB=shelves::top
geomA=iiwa::link7, geomB=shelves::shelf_lower
snopt_example=[ 0.5119587  -0.80097613  1.4041356 ], growth = 88.94239682323666
geomA=wsg::body_collision, geomB=shelves::shelf_lower
geomA=wsg::left_collision, geomB=shelves::shelf_lower
snopt_example=[ 0.27896158 -0.8160305   0.60048261], growt

geomA=wsg::body_collision, geomB=shelves::top
snopt_example=[ 0.03898991 -1.0702109  -0.17559755], growth = 4.176028989953181
geomA=wsg::body_collision, geomB=shelves::shelf_upper
snopt_example=[ 0.14420559 -1.25506828 -0.25494605], growth = 3.585332366144627
geomA=wsg::left_collision, geomB=shelves::top
snopt_example=[-0.04434811 -1.22664273 -0.13630201], growth = 0.8715330056431299
snopt_example=[-0.01399985 -0.99501865  0.0385244 ], growth = 9.19832182806266
geomA=wsg::right_collision, geomB=shelves::top
geomA=iiwa::link7, geomB=shelves::shelf_lower
geomA=wsg::body_collision, geomB=shelves::shelf_lower
geomA=wsg::left_collision, geomB=shelves::shelf_lower
geomA=wsg::right_collision, geomB=shelves::shelf_lower
geomA=iiwa::link7, geomB=wsg::left_collision
geomA=iiwa::link7, geomB=shelves::shelf_upper
geomA=wsg::left_collision, geomB=shelves::shelf_upper
0
geomA=iiwa::link7, geomB=shelves::top
geomA=iiwa::link7, geomB=wsg::right_collision
geomA=wsg::left_collision, geomB=wsg::right_col

# Choose poly to cert

In [17]:
poly_to_cert_safe = regions[2]
Atmp = poly_to_cert_safe.A()
btmp = poly_to_cert_safe.b()
poly_to_cert_safe = HPolyhedron(Atmp, btmp-0.3)


poly_to_cert_unsafe = regions[0]
Atmp = poly_to_cert_unsafe.A()
btmp = poly_to_cert_unsafe.b()
poly_to_cert_unsafe = HPolyhedron(Atmp, btmp+0.3)



## Plot Regions

In [18]:
def inpolycheck(q0,q1,q2, A, b):
    q = np.array([q0, q1, q2])
    res = np.min(1.0*(A@q-b<=0))
    #print(res)
    return res
eps = 0.5
meshes = []
col1 = 0x002BFF
col2 = 0x3EFF00 
idx = 0
step = 1/(1.0*len(regions))
R = np.array([[1, 0, 0],[0, 0, 1],[0,1, 0]])
order = (0,1,2)
for i, region in enumerate(regions):
    A = region.A()[:,order]
    b = region.b()

    col_hand = partial(inpolycheck, A=A, b=b)
    vertices, triangles = mcubes.marching_cubes_func(tuple(t_low-eps), tuple(t_high+eps), 50, 50, 50, col_hand, 0.5)

    regstr = "regions" +str(idx)
    ellstr = "ellipse" +str(idx)
    mat = meshcat.geometry.MeshLambertMaterial(color= int((1-idx*step)*col1 + idx*step*col2), wireframe=True)
    vis2['regions'][regstr].set_object(
            meshcat.geometry.TriangularMeshGeometry(vertices, triangles),
            mat)


    
    idx+=1
A_poly = poly_to_cert_safe.A()         
b_poly = poly_to_cert_safe.b() 
col_hand = partial(inpolycheck, A=A_poly, b=b_poly)
Nhere = 75
vertices, triangles = mcubes.marching_cubes_func(tuple(t_low-eps), tuple(t_high+eps), Nhere, Nhere, Nhere, col_hand, 0.5)
mat = meshcat.geometry.MeshLambertMaterial(color= int((1-idx*step)*col1 + idx*step*col2), wireframe=True)
mat.opacity = 0.3
vis2['poly_to_cert_safe'].set_object(
            meshcat.geometry.TriangularMeshGeometry(vertices, triangles),
            mat)
    
A_poly = poly_to_cert_unsafe.A()         
b_poly = poly_to_cert_unsafe.b() 
col_hand = partial(inpolycheck, A=A_poly, b=b_poly)
vertices, triangles = mcubes.marching_cubes_func(tuple(t_low), tuple(t_high), Nhere, Nhere, Nhere, col_hand, 0.5)
mat = meshcat.geometry.MeshLambertMaterial(color= int((1-idx*step)*col1 + idx*step*col2), wireframe=True)
mat.opacity = 0.3
vis2['poly_to_cert_unsafe'].set_object(
            meshcat.geometry.TriangularMeshGeometry(vertices, triangles),
            mat)

In [19]:
#monomial generation helpers
from pydrake.all import GenerateMonomialBasisOrderAllUpToOneExceptOneUpToTwo, GenerateMonomialBasisWithOrderUpToOne
print(GenerateMonomialBasisOrderAllUpToOneExceptOneUpToTwo(sym.Variables(t_kin)))
print(GenerateMonomialBasisWithOrderUpToOne(sym.Variables(t_kin)))


[<Monomial "1"> <Monomial "t[0]"> <Monomial "t[1]">
 <Monomial "t[0] * t[1]"> <Monomial "t[2]"> <Monomial "t[0] * t[2]">
 <Monomial "t[1] * t[2]"> <Monomial "t[0] * t[1] * t[2]">
 <Monomial "t[0]^2"> <Monomial "t[0]^2 * t[1]"> <Monomial "t[0]^2 * t[2]">
 <Monomial "t[0]^2 * t[1] * t[2]"> <Monomial "t[1]^2">
 <Monomial "t[0] * t[1]^2"> <Monomial "t[1]^2 * t[2]">
 <Monomial "t[0] * t[1]^2 * t[2]"> <Monomial "t[2]^2">
 <Monomial "t[0] * t[2]^2"> <Monomial "t[1] * t[2]^2">
 <Monomial "t[0] * t[1] * t[2]^2">]
[<Monomial "1"> <Monomial "t[0]"> <Monomial "t[1]">
 <Monomial "t[0] * t[1]"> <Monomial "t[2]"> <Monomial "t[0] * t[2]">
 <Monomial "t[1] * t[2]"> <Monomial "t[0] * t[1] * t[2]">]


# Certify the Regions

In [83]:
def construct_first_order_separating_hyperplane(prog, t, order = 2, plane_name = ''):
    if plane_name != '':
        plane_name = '_'+plane_name
    t_basis = sym.MonomialBasis(t, order)
    t_basis = np.array([sym.Polynomial(v) for v in t_basis])
    a_A_coeffs = prog.NewContinuousVariables(3, t_basis.shape[0], 'a_A'+plane_name)
#     a_b_offset = prog.NewContinuousVariables(3, 'a_b'+plane_name)
    a_poly = a_A_coeffs@t_basis#+a_b_offset
    b_A_coeffs = prog.NewContinuousVariables(1, t_basis.shape[0], 'b_A'+plane_name)
#     b_b_offset = prog.NewContinuousVariables(1, 'b_b'+plane_name)
    b_poly = b_A_coeffs@t_basis#+b_b_offset
    
    for i, p in enumerate(a_poly):
#         a_poly[i] = sym.Polynomial(p)
        a_poly[i].SetIndeterminates(sym.Variables(t))
    for i, p in enumerate(b_poly):
#       b_poly[i] = sym.Polynomial(p)
        b_poly[i].SetIndeterminates(sym.Variables(t))
#     prog.Add2NormSquaredCost(np.eye(3*t.shape[0]), np.zeros(3), a_A_coeffs)
#     dec_vars = [*a_A_coeffs.flatten().tolist(), *a_b_offset.tolist(), *b_A_coeffs.flatten().tolist(), *b_b_offset.tolist()]
    dec_vars = [*a_A_coeffs.flatten().tolist(), *b_A_coeffs.flatten().tolist()]

    return prog, a_poly, b_poly.item(), dec_vars


def putinarPsatConstraint(prog, p, t,  
                         poly_to_cert, lagrange_mult_degree = 2, var_epsilon = None):
    A = poly_to_cert.A()
    b = poly_to_cert.b()
    n = b.shape[0]
    if var_epsilon is None:
        var_epsilon = np.zeros(n)
#     lagrange_poly, Q = prog.NewSosPolynomial(sym.Variables(t), lagrange_mult_degree)
    lagrange_poly, Q = prog.NewSosPolynomial(GenerateMonomialBasisOrderAllUpToOneExceptOneUpToTwo(sym.Variables(t_kin)))
    lagrange_poly.SetIndeterminates(sym.Variables(t))
    prog.AddSosConstraint(lagrange_poly)
    constraint_poly = lagrange_poly
    for i in range(n):
#         lagrange_poly, Q = prog.NewSosPolynomial(sym.Variables(t), lagrange_mult_degree)
        lagrange_poly, Q = prog.NewSosPolynomial(GenerateMonomialBasisOrderAllUpToOneExceptOneUpToTwo(sym.Variables(t_kin)))
        lagrange_poly.SetIndeterminates(sym.Variables(t))
        prog.AddSosConstraint(lagrange_poly)
        constraint_poly += lagrange_poly*sym.Polynomial(b[i]-var_epsilon[i]-A[i,:]@t)
    constraint_poly.SetIndeterminates(sym.Variables(t))
    prog.AddEqualityConstraintBetweenPolynomials(constraint_poly, p-1e-10)
#     prog.AddSosConstraint(p-constraint_poly)
    return prog


def makeBodyHyperplaneSidePolynomials(prog, a_plane_poly, b_plane_poly,
                          VPoly, R_WA, p_WA, t, poly_to_cert, leq_or_geq,
                          lagrange_mult_degree = 2, var_epsilon = None, base_point_as_multilinear_poly = None):
    num_verts = VPoly.vertices().shape[1]

    vertex_pos = R_WA@(VPoly.vertices())+ np.repeat(p_WA[:, np.newaxis],num_verts,1)
    zero_poly = sym.Polynomial(0)
    if base_point_as_multilinear_poly is None:
        base_point_as_multilinear_poly = np.array([zero_poly for i in range(3)])
    
    centered_pos = vertex_pos #- np.repeat(base_point_as_multilinear_poly[:, np.newaxis],num_verts,1)
    
    dens = np.ndarray(shape = vertex_pos.shape,dtype = object)
    nums = np.ndarray(shape = vertex_pos.shape,dtype = object)
    for i, row in enumerate(vertex_pos):
        
        for j, v in enumerate(row):
            vertex_pos[i,j] = forward_kin.ConvertMultilinearPolynomialToRationalFunction(v)
            dens[i,j] = vertex_pos[i,j].denominator()
            nums[i,j] = vertex_pos[i,j].numerator()

    for c in range(dens.shape[1]):
        for r in range(dens.shape[0]-1):
            if not dens[r,c].EqualTo(dens[r+1,c]):
                raise ValueError("problem")
            
#     plane_rats = a_plane_poly.dot(vertex_pos)
    plane_polys = np.array([None for _ in range(vertex_pos.shape[1])])
    prog_eps = 1e-12
    for i in range(vertex_pos.shape[1]):
#         p.SetIndeterminates(sym.Variables(t))
        
        if leq_or_geq == 'leq':
            #a^Tx + b <= -1 -> -(a^Tx+b+1)>=0
            plane_polys[i] = (-a_plane_poly.dot(nums[:,i])-(b_plane_poly+1)*(dens[:,i].sum()))
            # (b_plane_poly-prog_eps)*p.denominator()-p.numerator() 
            # (b_plane_poly-prog_eps)*p.denominator()-p.numerator()
        elif leq_or_geq == 'geq':
            #a^Tx+b >= 1 -> a^Tx+b -1 >= 0
            plane_polys[i] = (a_plane_poly.dot(nums[:,i])+(b_plane_poly-1)*(dens[:,i].sum()))
        else:
            raise ValueError("leq_or_geq arg must be leq or geq not {}".format(leq_or_geq))  
        plane_polys[i].SetIndeterminates(sym.Variables(t))
        
#     plane_rats = a_plane_poly.dot(vertex_pos)
#     plane_polys2 = np.array([None for _ in plane_rats])
#     prog_eps = 1e-12
#     for i, p in enumerate(plane_rats):
#         p.SetIndeterminates(sym.Variables(t))

#         if leq_or_geq == 'leq':
#             #a^Tx + b <= -1 -> -(a^Tx+b+1)>=0
#             plane_polys2[i] = (-(p.numerator()+(b_plane_poly+1)*p.denominator())).item()
#             # (b_plane_poly-prog_eps)*p.denominator()-p.numerator() 
#             # (b_plane_poly-prog_eps)*p.denominator()-p.numerator()
#         elif leq_or_geq == 'geq':
#             #a^Tx+b >= 1 -> a^Tx+b -1 >= 0
#             plane_polys2[i] = (p.numerator()+(b_plane_poly-1)*p.denominator()).item()
#         else:
#             raise ValueError("leq_or_geq arg must be leq or geq not {}".format(leq_or_geq))  
#     for (p,q) in zip(plane_polys, plane_polys2):
#         print(p.EqualTo(q))
    return plane_polys


def add_pair_constraint(geomA, geomB, prog, poly_to_cert, 
                        lagrange_mult_degree = 2, var_epsilon = None):
    VPolyA, VPolyB = VPolyhedronSets[geomA], VPolyhedronSets[geomB]
    prog, a_plane_poly, b_plane_poly, dec_vars = construct_first_order_separating_hyperplane(prog, t_kin)
        
    R_WA, p_WA = X_WA_multilinear_list[int(body_indexes_by_geom_id[geomA])]
    R_WB, p_WB  = X_WA_multilinear_list[int(body_indexes_by_geom_id[geomB])]
    
    base_point_poly = None#R_WA@VPolyA.vertices().mean(axis = 1)-p_WA
#     base_point = np.array([forward_kin.ConvertMultilinearPolynomialToRationalFunction(p) for p in base_point_poly])
    
    
    plane_polys_A = makeBodyHyperplaneSidePolynomials(prog, a_plane_poly, b_plane_poly, 
                                                     VPolyA, R_WA, p_WA , t_kin, 
                                                     poly_to_cert, 'leq', lagrange_mult_degree,
                                                     var_epsilon, base_point_poly)
    plane_polys_B = makeBodyHyperplaneSidePolynomials(prog, a_plane_poly, b_plane_poly,
                                                     VPolyB, R_WB, p_WB , t_kin, 
                                                     poly_to_cert, 'geq', lagrange_mult_degree,
                                                     var_epsilon, base_point_poly)
    plane_polys = np.array(plane_polys_A.tolist()+ plane_polys_B.tolist()).squeeze()
    
    
    
    for p in plane_polys:
        prog = putinarPsatConstraint(prog, p, t_kin,  
                         poly_to_cert, lagrange_mult_degree = lagrange_mult_degree, var_epsilon = var_epsilon)
    return prog, plane_polys, (a_plane_poly, b_plane_poly), dec_vars


def construct_region_safety_problem(poly_to_cert, lagrange_mult_degree = 2, var_epsilon = None, check_archimedean = True, plane_name = ""):
    
    if check_archimedean:
        is_Archimedean,_ = certify_archimedean(poly_to_cert, t_kin)
        if not is_Archimedean:
            raise ValueError("region is not archimedean")
    prog = MathematicalProgram()
    prog.AddIndeterminates(t_kin)
    plane_pairs = {}
    plane_polys_list = []
    dec_vars = []
    for i, (geomA, geomB) in enumerate(pairs):
        print("pair {}/{}".format(i+1, len(pairs)))
        prog, plane_polys, (a_poly, b_poly), dec_vars0 = add_pair_constraint(geomA, geomB,
                                                       prog, poly_to_cert_safe,
                                                       lagrange_mult_degree = lagrange_mult_degree,
                                                       var_epsilon = var_epsilon
                                                      )
        plane_polys_list.append(plane_polys)
        plane_pairs[(geomA, geomB)] = (a_poly, b_poly)
        dec_vars += dec_vars0
#         if i >= 1:
#             break
    return prog, plane_pairs, plane_polys_list, np.array(dec_vars)

def certify_region(poly_to_cert, lagrange_mult_degree = 4, var_epsilon = None, check_archimedean = True, numeric_tol = 1e-10):
    prog, plane_pairs, plane_polys_list, dec_vars = construct_region_safety_problem(poly_to_cert, 
                                                                          lagrange_mult_degree = lagrange_mult_degree, 
                                                                          var_epsilon = var_epsilon, 
                                                                          check_archimedean = check_archimedean)
    result = convSolver.Solve(prog)
    numerically_cert = result.is_success() and (np.linalg.norm(result.GetSolution(dec_vars))>= numeric_tol)
    print(np.linalg.norm(result.GetSolution(dec_vars)))
    return numerically_cert, result, prog
              
def certify_archimedean(poly_to_cert, t, lagrange_mult_degree = 2):
    convSolver = MosekSolver()
    prog = MathematicalProgram()
    prog.AddIndeterminates(t)
        
    t_bar = sym.Polynomial(t@t)

    poly = t_bar
    A = poly_to_cert.A()
    b = poly_to_cert.b()
    n = b.shape[0]
    for i in range(n):
        lagrange_poly, Q = prog.NewSosPolynomial(sym.Variables(t), lagrange_mult_degree)
        lagrange_poly.SetIndeterminates(sym.Variables(t))
        prog.AddSosConstraint(lagrange_poly)
        poly += lagrange_poly*sym.Polynomial(b[i] - A[i,:]@t)
    poly.SetIndeterminates(sym.Variables(t))
    prog.AddSosConstraint(poly)
    result = convSolver.Solve(prog)
    return result.is_success(), prog


In [79]:
#safe
prog = MathematicalProgram()
convSolver = MosekSolver()
prog.AddIndeterminates(t_kin)
is_Archimedean,_ = certify_archimedean(poly_to_cert_safe, t_kin)
print("Poly to cert safe is Archimedean {}".format(is_Archimedean))
safe = True
safe_failures = []

max_iter = 1
iter_num = 0

eps = 0
safe = False
plane_pairs = []
while iter_num < max_iter:
    prog, plane_pairs, plane_polys_list, dec_vars = construct_region_safety_problem(poly_to_cert_safe, 
                                    lagrange_mult_degree = 10, 
                                    var_epsilon = eps*np.ones_like(poly_to_cert_safe.b()), 
                                    check_archimedean = True, 
                                    plane_name = "")
    result = convSolver.Solve(prog)
    print("Var_epsilon = {}, safe = {}".format(eps, result.is_success()))
    if result.is_success():
        safe = True
        break
    else:
        eps += 0.1
        iter_num += 1
print("Safe = {}".format(result.is_success()))
print("Plane vars norm {}".format(np.linalg.norm(result.GetSolution(dec_vars))))
    
#     if not result.is_success():
#         safe_failures += (geomA, geomB)
#     safe = safe and result.is_success()
# print(safe)

Poly to cert safe is Archimedean True
pair 1/15
pair 2/15
Var_epsilon = 0, safe = True
Safe = True
Plane vars norm 40852.99159729411


In [85]:
def extract_planes(plane_pairs):
    resulting_plane_pairs = {}
    
    for k, (a, b) in plane_pairs.items():
        a_list = []
        for ai in a:
            a_list.append(result.GetSolution(ai))
        resulting_plane_pairs[k] = (np.array(a_list), result.GetSolution(b))
    return resulting_plane_pairs

def EvaluatePlanePair(plane_pair, eval_dict):
    a_res = []
    for ai in plane_pair[0]:
        print(eval_dict)
        print(ai)
        a_res.append(ai.Evaluate(eval_dict))
    return (np.array(a_res), plane_pair[1].Evaluate(eval_dict))

cur_t = np.array([0.57,-0.73,0.37])
planes = extract_planes(plane_pairs)
print(EvaluatePlanePair(planes[next(iter(pairs))], dict(zip(sym.Variables(t_kin), cur_t))))
print(poly_to_cert_unsafe.A()@cur_t <= poly_to_cert_unsafe.b())



{Variable('t[0]', Continuous): 0.57, Variable('t[1]', Continuous): -0.73, Variable('t[2]', Continuous): 0.37}
4385.2494246949391*1 + 51.146254089372164*t[2] + 859.297206609211*t[2]^2 + 507.34597434043354*t[1] + 759.38218034890247*t[1] * t[2] + 1972.2548375488359*t[1]^2 + -1988.7937369324086*t[0] + -292.27962591164714*t[0] * t[2] + 3346.2057138034043*t[0] * t[1] + 1549.6724093522807*t[0]^2
{Variable('t[0]', Continuous): 0.57, Variable('t[1]', Continuous): -0.73, Variable('t[2]', Continuous): 0.37}
2.4042072119591776e-10*1 + 2.1621866225414819e-10*t[2] + -9.0992432281827759e-11*t[2]^2 + -2.8778932562943718e-10*t[1] + 4.9570648004035422e-11*t[1] * t[2] + 1.1264968781232801e-11*t[1]^2 + -3.2216812987575616e-10*t[0] + -8.5302125721485126e-11*t[0] * t[2] + 1.661283089733501e-10*t[0] * t[1] + -6.722815381053223e-11*t[0]^2
{Variable('t[0]', Continuous): 0.57, Variable('t[1]', Continuous): -0.73, Variable('t[2]', Continuous): 0.37}
-1215.1804489324597*1 + -889.20374933041967*t[2] + 329.23365066

In [ ]:
for (a,b) in plane_pairs:
    for i in range(3):
        for a_coeff in a[i].decision_variables():
            print(result.GetSolution(a_coeff))
        for b_coeff in b.decision_variables():
            print(result.GetSolution(b_coeff))
    print()
res = result.GetSolution()
print(np.linalg.norm(res))

In [84]:
# unsafe
is_Archimedean,_ = certify_archimedean(poly_to_cert_unsafe, t_kin)
print("Poly to cert safe is Archimedean {}".format(is_Archimedean))

# prog = MathematicalProgram()
# prog.AddIndeterminates(t)
# safe = True
# safe_failures = []
# prog = MathematicalProgram()
# prog.AddIndeterminates(t)
# plane_pairs = []
# plane_polys_list = []
prog, plane_pairs, plane_polys_list, dec_vars = construct_region_safety_problem(poly_to_cert_unsafe, 
                                    lagrange_mult_degree = 10, 
                                    var_epsilon = None, 
                                    check_archimedean = True, 
                                    plane_name = "")
result = convSolver.Solve(prog)
print("Safe = {}".format(result.is_success()))
print("Plane vars norm {}".format(np.linalg.norm(result.GetSolution(dec_vars))))


Poly to cert safe is Archimedean True
pair 1/15
pair 2/15
pair 3/15
pair 4/15
pair 5/15
pair 6/15
pair 7/15
pair 8/15
pair 9/15
pair 10/15
pair 11/15
pair 12/15
pair 13/15
pair 14/15
pair 15/15
Safe = True
Plane vars norm 81653.54579959728


[<Polynomial "b_A(0,9)*1 + b_A(0,6)*t[2] + b_A(0,0)*t[2]^2 + b_A(0,7)*t[1] + b_A(0,1)*t[1] * t[2] + b_A(0,2)*t[1]^2 + b_A(0,8)*t[0] + b_A(0,3)*t[0] * t[2] + b_A(0,4)*t[0] * t[1] + b_A(0,5)*t[0]^2">]


TypeError: GetSolution(): incompatible function arguments. The following argument types are supported:
    1. (self: pydrake.solvers.mathematicalprogram.MathematicalProgramResult) -> numpy.ndarray[numpy.float64[m, 1]]
    2. (self: pydrake.solvers.mathematicalprogram.MathematicalProgramResult, arg0: pydrake.symbolic.Variable) -> float
    3. (self: pydrake.solvers.mathematicalprogram.MathematicalProgramResult, arg0: numpy.ndarray[object[m, 1]]) -> numpy.ndarray[numpy.float64[m, 1]]
    4. (self: pydrake.solvers.mathematicalprogram.MathematicalProgramResult, arg0: numpy.ndarray[object[m, n]]) -> numpy.ndarray[numpy.float64[m, n]]
    5. (self: pydrake.solvers.mathematicalprogram.MathematicalProgramResult, arg0: pydrake.symbolic.Expression) -> pydrake.symbolic.Expression
    6. (self: pydrake.solvers.mathematicalprogram.MathematicalProgramResult, arg0: pydrake.symbolic.Polynomial) -> pydrake.symbolic.Polynomial
    7. (self: pydrake.solvers.mathematicalprogram.MathematicalProgramResult, 

In [ ]:
res = result.GetSolution()
print(np.linalg.norm(res))

In [ ]:
print(np.array(plane_polys_list).shape)

In [ ]:

convSolver = MosekSolver()
is_Archimedean,_ = certify_archimedean(poly_to_cert_unsafe, t_kin)
print("Poly to cert safe is Archimedean {}".format(is_Archimedean))
start_time = time.time()
failures = []
for j,r in enumerate(regions):
    print("Region {}/{}".format(j, len(regions)-1))
    rtmp = HPolyhedron(r.A(), r.b()+0.5)
    numerically_cert, result, prog = certify_region(rtmp, 
                                                    lagrange_mult_degree = 4,
                                                    check_archimedean = True,
                                                    numeric_tol = 1e-10)
    print("Safe: {}".format(numerically_cert))
    if not numerically_cert:
        failures += [r]
end_time = time.time()
print("Certified in {}".format(end_time-start_time))

In [76]:
# certify region is P compact
i, (geomA, geomB) = next(iter(enumerate(pairs)))
R_WA, p_WA = X_WA_multilinear_list[int(body_indexes_by_geom_id[geomA])]
R_WA, p_WA = R_WA.copy(), p_WA.copy()
X_WA_rat_direct = X_WA_list[int(body_indexes_by_geom_id[geomA])]
R_WA_direct, p_WA_direct = X_WA_rat_direct.rotation().matrix(), X_WA_rat_direct.translation()

for i in range(3):
    for j in range(3):
        R_WA[i,j] = forward_kin.ConvertMultilinearPolynomialToRationalFunction(R_WA[i,j])
    p_WA[i] = forward_kin.ConvertMultilinearPolynomialToRationalFunction(p_WA[i])

num_samp = 10000
bad_evals = {}
num_bad = 0
for i in range(num_samp):
    t_vals = np.random.uniform(t_low, t_high, (3,))
    vals_dict = dict(zip(sym.Variables(t_kin), t_vals))
    conv_R = np.zeros_like(R_WA)
    conv_p = np.zeros_like(p_WA)
    direct_R = np.zeros(R_WA.shape).astype(float)
    direct_p = np.zeros(p_WA.shape).astype(float)
    for i in range(3):
        for j in range(3):
            conv_R[i,j] = R_WA[i,j].numerator().Evaluate(vals_dict)/R_WA[i,j].denominator().Evaluate(vals_dict)
            direct_R[i,j] = R_WA_direct[i,j].Evaluate(vals_dict)
            
        conv_p[i] = p_WA[i].numerator().Evaluate(vals_dict)/p_WA[i].denominator().Evaluate(vals_dict)
        direct_p[i] = p_WA_direct[i].Evaluate(vals_dict)

        if not np.allclose(conv_R.astype(float), direct_R.astype(float))  or not np.allclose(conv_p.astype(float), direct_p.astype(float)) :
            bad_evals[t_vals] = ((conv_R, direct_R), (conv_p, direct_p))
            num_bad += 1
            print(num_bad)
print("done")  

done


In [53]:
vals_dict = dict(zip(sym.Variables(t_kin), [0,0,0]))
R_WA_direct.Evaluate(vals_dict)

AttributeError: 'numpy.ndarray' object has no attribute 'Evaluate'

In [86]:
import scipy 
import utils

x = np.linspace(-1,1, 10)
y = np.linspace(-1,1, 10)
verts = []

for idxx in range(len(x)):
    for idxy in range(len(y)):
        verts.append(np.array([x[idxx], y[idxy]]))
       
tri = scipy.spatial.Delaunay(verts)
plane_triangles = tri.simplices
plane_verts = tri.points[:,:]
plane_verts = np.concatenate((plane_verts, 0*plane_verts[:,0].reshape(-1,1)), axis = 1)

def transform(a,b, p1, p2, plane_verts, plane_triangles):
    alpha = (b-a.T@p1)/(a.T@(p2-p1))
    print(alpha)
    offset = alpha*(p2-p1) + p1
    z = np.array([0, 0, 1])
    crossprod = np.cross(utils.normalize(a), z)
    if np.linalg.norm(crossprod) <=1e-4:
        R = np.eye(3)
    else:
        ang = np.arcsin(np.linalg.norm(crossprod))
        axis = utils.normalize(crossprod)
        R = utils.get_rotation_matrix(axis, -ang)
        
    verts_tf = (R@plane_verts.T).T + offset
    return verts_tf

def transform_at_t(cur_t, a_poly, b_poly, p1_rat, p2_rat):
    eval_dict = dict(zip(sym.Variables(t_kin), cur_t))
    a,b = EvaluatePlanePair((a_poly, b_poly), eval_dict)
    print(f"{a}, {b}")
    p1 = np.array([p.Evaluate(eval_dict) for p in p1_rat])
    p2 = np.array([p.Evaluate(eval_dict) for p in p2_rat])
    return transform(a,b, p1, p2, plane_verts, plane_triangles), p1, p2

def transform_plane_geom_id(geomA, geomB, planes_dict, cur_t):
    vA = t_space_vertex_position_by_geom_id[geomA][:,0]
    vB = t_space_vertex_position_by_geom_id[geomB][:,0]
    a_poly, b_poly = planes_dict[(geomA, geomB)]
    return transform_at_t(cur_t, a_poly, b_poly, vA, vB)

def plot_plane_geom_id(geomA, geomB, planes_dict, cur_t):
    verts_tf, p1, p2 = transform_plane_geom_id(geomA, geomB, planes_dict, cur_t)
    mat = meshcat.geometry.MeshLambertMaterial(color=utils.rgb_to_hex((255,0,0)), wireframe=False)
    mat.opacity = 0.5
    vis["plane"][f"{geomA.get_value()}, {geomB.get_value()}"].set_object(
                meshcat.geometry.TriangularMeshGeometry(verts_tf, plane_triangles),
                mat)
    
    mat.opacity = 1.0
    utils.plot_point(loc = p1, radius = 0.05, mat = mat, vis = vis["plane"][f"{geomA.get_value()}, {geomB.get_value()}"], marker_id= 'p1')
    mat = meshcat.geometry.MeshLambertMaterial(color=utils.rgb_to_hex((255,255,0)), wireframe=False)
    mat.opacity = 1.0
    utils.plot_point(loc = p2, radius = 0.05, mat = mat, vis = vis["plane"][f"{geomA.get_value()}, {geomB.get_value()}"], marker_id= 'p2')


cur_t = np.array([0.57,-0.73,0.37])
showres_t(cur_t)
planes = extract_planes(plane_pairs)

def plane_callback(t):
    for geomA, geomB in planes.keys():
        plot_plane_geom_id(geomA, geomB, planes, t)


# Comments with Hongkai
1.) To reduce poly size always get transforms relative to middle link in kinematic chain between two bodies (not worried)

2.) make the hyperplane an affine function of t. Should allow plane to rotate

3.) Do line search on Ct <= b- epsilon to scale regions

4.) Rational polynomials should have coordinate degree 2. Track down this bug ASAP
